In [2]:
! sudo apt install openjdk-8-jdk
! sudo update-alternatives --set java /usr/lib/jvm/java-8-openjdk-amd64/jre/bin/java 
! pip install language-check -qq
! pip install pycontractions -qq

Reading package lists... Done
Building dependency tree       
Reading state information... Done
openjdk-8-jdk is already the newest version (8u242-b08-0ubuntu3~18.04).
0 upgraded, 0 newly installed, 0 to remove and 25 not upgraded.
update-alternatives: using /usr/lib/jvm/java-8-openjdk-amd64/jre/bin/java to provide /usr/bin/java (java) in manual mode


In [0]:
# Import statements
import pandas as pd
import numpy as np
import pprint as pp
import json
from pandas.io.json import json_normalize
import re
from timeit import default_timer

# Preprocessing
from pycontractions import Contractions

# Tokenization imports
import nltk
from nltk.tokenize import sent_tokenize
from nltk.tokenize import word_tokenize

# Puncuation & lower case
import string #punctuation removal

# Stop words
from nltk.corpus import stopwords

# Stemming
from nltk.stem.snowball import SnowballStemmer

# Lemmatizer
from nltk.stem.wordnet import WordNetLemmatizer

# POS tagging
from nltk.corpus import wordnet

# NER
import nltk, nltk.tag, nltk.chunk 
import spacy
import pprint as pprint
from gensim.summarization import summarize 
from collections import Counter 
import en_core_web_sm # CNN gets loaded in, sees what words depends on each other, POS tagging, entity recognition 
from spacy import displacy # Visualize NER

# Data extraction

In [0]:
# Load JSON file into dataframe
data = pd.read_json('/content/drive/My Drive/frames.json')
df = pd.DataFrame(data)

In [4]:
df.head() # Looks like turns and labels are nested dictionaries

user_id  ...                                             labels
0  U22HTHYNP  ...  {'userSurveyRating': 4.0, 'wizardSurveyTaskSuc...
1  U21E41CQP  ...  {'userSurveyRating': 3.0, 'wizardSurveyTaskSuc...
2  U21RP4FCY  ...  {'userSurveyRating': 2.0, 'wizardSurveyTaskSuc...
3  U22HTHYNP  ...  {'userSurveyRating': 5.0, 'wizardSurveyTaskSuc...
4  U21E41CQP  ...  {'userSurveyRating': 5.0, 'wizardSurveyTaskSuc...

[5 rows x 5 columns]

In [5]:
df['id'].nunique() # There are 1369 unique ID for the dialogue

1369

In [0]:
# labels is a nested dictionary
labels_df = json_normalize(df['labels'])

In [7]:
labels_df.head()

userSurveyRating  wizardSurveyTaskSuccessful
0               4.0                        True
1               3.0                        True
2               2.0                       False
3               5.0                        True
4               5.0                        True

`userSurveyRating` - value that represents the user’s satisfaction with the Wizard’s service, ranging from 1 – complete dissatisfaction to 5 – complete satisfaction

`wizardSurveyTaskSuccessful` - boolean which is true if the wizard thinks at the end of the dialogue that the user’s goal was achieved

In [0]:
# Attempted json_normalize but kept getting the error: 'list' object has no attribute 'values'
# This happens because of list enclosing each of the dictionary.
#   - Multiple dictionaries with matching keys enclosed by a list.
#   - A dictionary with keys as columns and values in the form of list.

# Thus we try another approach
text_list = []
for item in df['turns']:
  text_list.append(item)
turns_df = pd.DataFrame(text_list)

In [9]:
turns_df.head(2) # Every row is a dialogue 

0  ...    47
0  {'text': 'I'd like to book a trip to Atlantis ...  ...  None
1  {'text': 'Hello, I am looking to book a vacati...  ...  None

[2 rows x 48 columns]

In [0]:
turns_df.replace(np.nan,'',inplace=True) # Replace all null values

In [0]:
turns_df_T = turns_df.transpose() # Transposed the dataframe to have proper conversation turns

In [0]:
# Iterates through the data frame and gets all values with a text key
convo_text = ''
for i in turns_df_T:                                 # 1369 columns
  for j in range(0,48):                              # 48 rows
    try:
      get_text = turns_df_T[i][j].get('text')        # Gets the value from the corresponding key
      convo_text += get_text + ' '                   # Concatenates all text
    except AttributeError:
      convo_text += ''                               # Concatenates '' if there is no text key - used for switching conversations

# Data Preprocessing

In [0]:
with open('/content/drive/My Drive/expand_convo_text_full.txt', 'r') as file:
    convo_all = file.read()

In [8]:
# Conversation sample
pp.pprint(convo_all[0:898]) 

("['I would like to book a trip to Atlantis from Caprica on Saturday, August "
 '13, 2016 for 8 adults. I have a tight budget of 1700. Hi...I checked a few '
 'options for you, and unfortunately, we do not currently have any trips that '
 'meet this criteria.  Would you like to book an alternate travel option? Yes, '
 'how about going to Neverland from Caprica on August 13, 2016 for 5 adults. '
 'For this trip, my budget would be 1900. I checked the availability for this '
 'date and there were no trips available.  Would you like to select some '
 'alternate dates? I have no flexibility for dates... but I can leave from '
 'Atlantis rather than Caprica. How about that? I checked the availability for '
 'that date and there were no trips available.  Would you like to select some '
 'alternate dates? I suppose I will speak with my husband to see if we can '
 'choose other dates, and then I will come back to you.Thanks for your help ')


## Tokenization

In [9]:
nltk.download('punkt') # Punkt sentence tokenizer

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [11]:
#split into sentences
tokenized_sent = sent_tokenize(convo_all)
pp.pprint(tokenized_sent[0:5])

["['I would like to book a trip to Atlantis from Caprica on Saturday, August "
 '13, 2016 for 8 adults.',
 'I have a tight budget of 1700.',
 'Hi...I checked a few options for you, and unfortunately, we do not currently '
 'have any trips that meet this criteria.',
 'Would you like to book an alternate travel option?',
 'Yes, how about going to Neverland from Caprica on August 13, 2016 for 5 '
 'adults.']


In [12]:
len(tokenized_sent)

24091

In [13]:
#split into words
tokenized_words=[]
tokenized_words.extend(word for word in word_tokenize(str(tokenized_sent)))
pp.pprint(tokenized_words[0:40])

['[',
 '``',
 '[',
 "'I",
 'would',
 'like',
 'to',
 'book',
 'a',
 'trip',
 'to',
 'Atlantis',
 'from',
 'Caprica',
 'on',
 'Saturday',
 ',',
 'August',
 '13',
 ',',
 '2016',
 'for',
 '8',
 'adults',
 '.',
 '``',
 ',',
 "'I",
 'have',
 'a',
 'tight',
 'budget',
 'of',
 '1700',
 '.',
 "'",
 ',',
 "'Hi",
 '...',
 'I']


## Punctuation & Lower Case

In [0]:
string.punctuation = string.punctuation + '``' + '...'

In [15]:
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~``...'

In [16]:
# Removes punctuation
no_punct = [token for token in tokenized_words if token not in string.punctuation] 
print(no_punct[0:20])

["'I", 'would', 'like', 'to', 'book', 'a', 'trip', 'to', 'Atlantis', 'from', 'Caprica', 'on', 'Saturday', 'August', '13', '2016', 'for', '8', 'adults', "'I"]


In [17]:
# Lowercase text
data_lower = [word.lower() for word in no_punct]
print(data_lower[0:20])

["'i", 'would', 'like', 'to', 'book', 'a', 'trip', 'to', 'atlantis', 'from', 'caprica', 'on', 'saturday', 'august', '13', '2016', 'for', '8', 'adults', "'i"]


## Stop Words

In [18]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [19]:
stop_words = stopwords.words('english')
add_stop_words = ['\'i','would','could']
stop_words += add_stop_words
print(stop_words)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [0]:
filtered_word = []
for word in data_lower:
  if word not in stop_words:
    filtered_word.append(word)

In [21]:
filtered_word[0:20]

['like',
 'book',
 'trip',
 'atlantis',
 'caprica',
 'saturday',
 'august',
 '13',
 '2016',
 '8',
 'adults',
 'tight',
 'budget',
 '1700',
 "'hi",
 'checked',
 'options',
 'unfortunately',
 'currently',
 'trips']

## Stemming

In [0]:
stemmer = SnowballStemmer('english', ignore_stopwords=True) # Already removed stopwords

In [0]:
stemmed_words = []

for words in filtered_sent:
  
  stemmed_words.append(stemmer.stem(words)) 

  print('Words '+words+' - stemmer:'+stemmer.stem(words))

In [0]:
filtered_words = []
for word in stemmed_words:
  if word not in stop_words:
    filtered_words.append(word)

In [0]:
filtered_words

## Lemmatizing with appropriate POS tag

In [22]:
nltk.download('wordnet')                        # Lemmatization
nltk.download('averaged_perceptron_tagger')     # POS tagging

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

In [0]:
filtered_word = [word.strip('\'') for word in filtered_word] # Pesky ' attatched to word

In [0]:
filtered_word_2 = []
for word in filtered_word:
  if word not in stop_words:
    filtered_word_2.append(word)

In [25]:
pp.pprint(filtered_word_2[-10:])

['perfect',
 'book',
 'consider',
 'done',
 'good',
 'trip',
 'slightly_smiling_face',
 'thanks',
 'pleasure',
 '']


In [0]:
def get_wordnet_pos(word):
    """Map POS tag to first character lemmatize() accepts"""
    tag = nltk.pos_tag([word])[0][1][0].upper()
    tag_dict = {"J": wordnet.ADJ,
                "N": wordnet.NOUN,
                "V": wordnet.VERB,
                "R": wordnet.ADV}

    return tag_dict.get(tag, wordnet.NOUN)

In [0]:
lem_words = []
lem = WordNetLemmatizer()
lem_words = [lem.lemmatize(word, get_wordnet_pos(word)) for word in filtered_word_2 if word]

## NER

In [0]:
nlp = en_core_web_sm.load()

In [0]:
text = ' '.join(lem_words)

In [0]:
convo_nlp = nlp(text)

In [33]:
labels = [ent.label_ for ent in convo_nlp.ents]
Counter(labels)

Counter({'CARDINAL': 7435,
         'DATE': 4985,
         'EVENT': 155,
         'FAC': 404,
         'GPE': 3577,
         'LAW': 5,
         'LOC': 69,
         'MONEY': 170,
         'NORP': 38,
         'ORDINAL': 595,
         'ORG': 783,
         'PERCENT': 3,
         'PERSON': 763,
         'PRODUCT': 128,
         'QUANTITY': 49,
         'TIME': 167,
         'WORK_OF_ART': 19})

In [35]:
#Print a random sentence from these conversations 
sentences = [x for x in convo_nlp.sents]
print(sentences[12])

neverland find trip available neverland trip gotham city kobe original budget 2100


In [36]:
displacy.render(convo_nlp, jupyter=True, style='ent', page=True)